In [ ]:
%matplotlib inline

In [ ]:
import pandas as pd
from math import pi

from bokeh.models import ColumnDataSource
from bokeh.models import HoverTool
from bokeh.plotting import figure,  output_file, show

from bokeh.models import LinearAxis, Range1d
from bokeh.layouts import gridplot

from scipy.signal import detrend

In [ ]:
print("# pandas version = ",pd.__version__)

In [ ]:
import bokeh as bk
print("# bokeh version = ",bk.__version__)

In [ ]:
import scipy as sp
print("# scipy version = ",sp.__version__)

In [6]:
# ftp directory
donet_dir = "http://ncedc.org/ftp/outgoing/taira/DONET"

In [7]:
# sts1v data
kis_sts1v_fi = donet_dir + "/kis_sts1v_0.00001-0.01hz.300sps.acc.ts.wh.out"

In [8]:
print(kis_sts1v_fi)

http://ncedc.org/ftp/outgoing/taira/DONET/kis_sts1v_0.00001-0.01hz.300sps.acc.ts.wh.out


In [9]:
# pfo volumetric strain data. assuming poisson's ratio = 0.25
kis_evolume_fi = donet_dir + "/ez_volume_nu0.25_.ts.wh.out"

In [10]:
print(kis_evolume_fi)

http://ncedc.org/ftp/outgoing/taira/DONET/ez_volume_nu0.25_.ts.wh.out


In [11]:
# pfo gravitatity data
kis_grav_fi = donet_dir + "/KIS.grav.out.ts.wh.out"

In [12]:
# read file
# format
# time           acc (nano m/s*2)          
#2009-7-14T0:0:00 -53298
kis_sts1v =pd.read_csv(kis_sts1v_fi,
                          sep=" ",names=["time", "acc_nano"],
                          header=None, skiprows=1)
#print(hhz_psd_ts)

In [13]:
# convert "time" to datetime. need for plot
kis_sts1v['time'] = pd.to_datetime(kis_sts1v['time'])

In [14]:
len(kis_sts1v)

105408

In [15]:
# check
kis_sts1v.head()

time  acc_nano
0 2016-01-01 00:00:00     -2549
1 2016-01-01 00:05:00     -2512
2 2016-01-01 00:10:00     -2475
3 2016-01-01 00:15:00     -2439
4 2016-01-01 00:20:00     -2402

In [16]:
# check
kis_sts1v.tail()

time  acc_nano
105403 2016-12-31 23:35:00     -2814
105404 2016-12-31 23:40:00     -3143
105405 2016-12-31 23:45:00     -3484
105406 2016-12-31 23:50:00     -3837
105407 2016-12-31 23:55:00     -4204

In [17]:
# PFO strain data
# time vol ez0 (az=0deg) ez90 (az=90deg)
kis_evolume =pd.read_csv(kis_evolume_fi,
                          sep=",",names=["time", "vol","ez0","ez90"],
                          header=None, skiprows=1)

In [19]:
len(kis_evolume)

105408

In [20]:
kis_evolume.head()

time        vol      ez0     ez90
0  2016-01-01T00:00:00.0000  -9.939358 -8.64875 -6.26028
1  2016-01-01T00:05:00.0000 -10.260012 -8.93439 -6.45562
2  2016-01-01T00:10:00.0000 -10.565132 -9.20508 -6.64261
3  2016-01-01T00:15:00.0000 -10.856425 -9.46217 -6.82246
4  2016-01-01T00:20:00.0000 -11.133279 -9.70481 -6.99510

In [21]:
# time format conversion
kis_evolume['time'] = pd.to_datetime(kis_evolume['time'])

In [22]:
# PFO gravity data
# time                    gravity microgal, positive for decreasing    
# microgal = microgal2. same data
kis_grav =pd.read_csv(kis_grav_fi,
                          sep=" ",names=["time", "microgal", "microgal2"],
                          header=None, skiprows=1)

In [23]:
len(kis_grav)

105408

In [24]:
# microgal2 is Nan.... Not sure why but microgal2 is not used
kis_grav.head()

time  microgal  microgal2
0  2016-01-01T00:00:00.0000 -47.47725  -47.47725
1  2016-01-01T00:05:00.0000 -48.98182  -48.98182
2  2016-01-01T00:10:00.0000 -50.41110  -50.41110
3  2016-01-01T00:15:00.0000 -51.77316  -51.77316
4  2016-01-01T00:20:00.0000 -53.06521  -53.06521

In [25]:
# time format conversion
kis_grav['time'] = pd.to_datetime(kis_grav['time'])

In [26]:
# check
kis_grav['time'].head()

0   2016-01-01 00:00:00
1   2016-01-01 00:05:00
2   2016-01-01 00:10:00
3   2016-01-01 00:15:00
4   2016-01-01 00:20:00
Name: time, dtype: datetime64[ns]

In [27]:
# trim data
#kis_grav_select = kis_grav[("2016-01-01 00:00:00" <= kis_grav['time'])  &   (kis_grav['time'] <= "2016-04-01 00:00:00")]
kis_grav_select = kis_grav



In [28]:
# check
kis_grav_select.head()

time  microgal  microgal2
0 2016-01-01 00:00:00 -47.47725  -47.47725
1 2016-01-01 00:05:00 -48.98182  -48.98182
2 2016-01-01 00:10:00 -50.41110  -50.41110
3 2016-01-01 00:15:00 -51.77316  -51.77316
4 2016-01-01 00:20:00 -53.06521  -53.06521

In [32]:
# trim daat
#kis_evolume_select = kis_evolume[   ("2016-01-01 00:00:00" <= kis_evolume['time'])  &   
#                                 (kis_evolume['time'] <= "2016-04-01 00:00:00")   ]
kis_evolume_select=kis_evolume

In [33]:
# check
kis_evolume_select.head()

time        vol      ez0     ez90
0 2016-01-01 00:00:00  -9.939358 -8.64875 -6.26028
1 2016-01-01 00:05:00 -10.260012 -8.93439 -6.45562
2 2016-01-01 00:10:00 -10.565132 -9.20508 -6.64261
3 2016-01-01 00:15:00 -10.856425 -9.46217 -6.82246
4 2016-01-01 00:20:00 -11.133279 -9.70481 -6.99510

In [34]:
# dataframe to numpy matrix
evolume_matrix = kis_evolume_select.as_matrix()

/anaconda3/envs/netops/lib/python3.7/site-packages/ipykernel_launcher.py:2: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  


In [35]:
# check to see evol
evolume_matrix[:,1] # 0 time, 1 evol # 2 ez0 #3 ez90

array([-9.939358, -10.260012, -10.565132, ..., -18.260982000000002,
       -18.134729, -17.982049], dtype=object)

In [36]:
len(evolume_matrix)

105408

In [37]:
len(kis_sts1v)

105408

In [38]:
len(kis_evolume_select)

105408

In [39]:
# now add evol data as pfo_sts1v['vol']
kis_sts1v['vol'] =evolume_matrix[:,1] 

In [40]:
# check
kis_sts1v['vol'].head()

0   -9.93936
1     -10.26
2   -10.5651
3   -10.8564
4   -11.1333
Name: vol, dtype: object

In [41]:
# check
kis_sts1v['time'].head()

0   2016-01-01 00:00:00
1   2016-01-01 00:05:00
2   2016-01-01 00:10:00
3   2016-01-01 00:15:00
4   2016-01-01 00:20:00
Name: time, dtype: datetime64[ns]

In [42]:
# dataframe to numpy matrix
grav_matrix = kis_grav_select.as_matrix()

/anaconda3/envs/netops/lib/python3.7/site-packages/ipykernel_launcher.py:2: FutureWarning: Method .as_matrix will be removed in a future version. Use .values instead.
  


In [43]:
# check 
grav_matrix[:,1] # microgal

array([-47.47725, -48.98182, -50.4111, ..., -85.86583, -85.31617,
       -84.64220999999999], dtype=object)

In [44]:
# now add microgal data as pfo_sts1v['microgal']
kis_sts1v['microgal'] = grav_matrix[:,1]

In [45]:
# check
kis_sts1v['microgal'].head()

0   -47.4772
1   -48.9818
2   -50.4111
3   -51.7732
4   -53.0652
Name: microgal, dtype: object

In [51]:
#TOOLS = "pan,wheel_zoom,box_zoom,undo,reset,save"
TOOLS = "pan,box_zoom,undo,reset,save"

#data = {'x_values': [1, 2, 3, 4, 5],
#        'y_values': [6, 7, 2, 3, 6]}
 
# make "data". all parameters need to be added
 
data =  {
                'time': kis_sts1v['time'], 
               'acc_mili': kis_sts1v['acc_nano']/1000/1000, 
               'microgal': kis_sts1v['microgal'], 
                'vol': kis_sts1v['vol'], 

          #'time': kis_evolume['time'], 
}

# make source. needed
source = ColumnDataSource(data=data)


# x_axis is datetime. add tools. define size and add title
#p = figure(x_axis_type="datetime", tools=TOOLS, plot_width=600, height=600, title = "kis")
p = figure(x_axis_type="datetime", tools=TOOLS, plot_width=1000, height=600, title = "KIS")

# labels
p.xaxis.axis_label = 'Time (UTC)'
p.yaxis.axis_label = 'Acceleration (mm/s*2) '

# label orientation
p.xaxis.major_label_orientation = pi/4
# grid line
p.grid.grid_line_alpha=1.0

# define Y-range 
bottom, top = -5, 5
p.y_range=Range1d(bottom, top)

# plot STS1-v data
p.line(x='time', y='acc_mili', source=source,legend="STS1v")

# another Y-axis (right side)
p.extra_y_ranges = {"y2": Range1d(start=-160, end=60)}
# another Y-axis label
p.add_layout(LinearAxis(y_range_name="y2", axis_label='Nanostrain (positive extension)'), 'right')
# plot volumetric strain data with y2 axis
p.line(x='time', y='vol', y_range_name="y2", source=source,legend="Volumetric strain",line_color="black")


# font and etc
p.title.text_font="calibri"
p.title.text_font_size="20pt"
p.title.align="center"

p.xaxis.axis_label_text_font_size = "16pt"
p.xaxis.axis_label_text_font="calibri"
p.xaxis.major_label_text_font_size = "14pt"
p.xaxis.major_label_text_font="calibri"

p.yaxis.axis_label_text_font_size = "16pt"
p.yaxis.axis_label_text_font="calibri"
p.yaxis.major_label_text_font_size = "14pt"
p.yaxis.major_label_text_font="calibri"

p.xaxis.axis_label_text_font_style = 'normal'
p.yaxis.axis_label_text_font_style = 'normal'

p.xaxis[0].formatter.days = '%m/%d/%Y'


# save .html file
output_file("kis_ts.html", title="KIS")
# if you want to plot only "p"
#show(p)  # open a browser

# two figure with "vertical"
#grid = gridplot([[p], [p2]])
# two figure with "horizontal"
#grid = gridplot([[p,p2]])
grid = gridplot([[p]])

# will open a browser
show(grid)

